<a href="https://colab.research.google.com/github/omarcevi/ML-Projects/blob/main/simple_machine_translation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import tensorflow as tf
from pathlib import Path
print(tf.__version__)

2.15.0


In [2]:
url = "https://storage.googleapis.com/download.tensorflow.org/data/spa-eng.zip"
path = tf.keras.utils.get_file("spa-eng.zip", origin=url, cache_dir="datasets", extract=True)

2638744/2638744 [==============================] - 1s 0us/step


In [3]:
text = (Path(path).with_name("spa-eng") / "spa.txt").read_text()

In [4]:
text

'Go.\tVe.\nGo.\tVete.\nGo.\tVaya.\nGo.\tVáyase.\nHi.\tHola.\nRun!\t¡Corre!\nRun.\tCorred.\nWho?\t¿Quién?\nFire!\t¡Fuego!\nFire!\t¡Incendio!\nFire!\t¡Disparad!\nHelp!\t¡Ayuda!\nHelp!\t¡Socorro! ¡Auxilio!\nHelp!\t¡Auxilio!\nJump!\t¡Salta!\nJump.\tSalte.\nStop!\t¡Parad!\nStop!\t¡Para!\nStop!\t¡Pare!\nWait!\t¡Espera!\nWait.\tEsperen.\nGo on.\tContinúa.\nGo on.\tContinúe.\nHello!\tHola.\nI ran.\tCorrí.\nI ran.\tCorría.\nI try.\tLo intento.\nI won!\t¡He ganado!\nOh no!\t¡Oh, no!\nRelax.\tTomátelo con soda.\nSmile.\tSonríe.\nAttack!\t¡Al ataque!\nAttack!\t¡Atacad!\nGet up.\tLevanta.\nGo now.\tVe ahora mismo.\nGot it!\t¡Lo tengo!\nGot it?\t¿Lo pillas?\nGot it?\t¿Entendiste?\nHe ran.\tÉl corrió.\nHop in.\tMétete adentro.\nHug me.\tAbrázame.\nI fell.\tMe caí.\nI know.\tYo lo sé.\nI left.\tSalí.\nI lied.\tMentí.\nI lost.\tPerdí.\nI quit.\tDimito.\nI quit.\tRenuncié.\nI work.\tEstoy trabajando.\nI\'m 19.\tTengo diecinueve.\nI\'m up.\tEstoy levantado.\nListen.\tEscucha.\nListen.\tEscuche.\nListen.\

In [5]:
import numpy as np

In [6]:
text = text.replace("¡", "").replace("¿", "")
pairs = [line.split("\t") for line in text.splitlines()]
np.random.shuffle(pairs)

In [7]:
sentences_en, sentences_es = zip(*pairs)

In [8]:
for i in range(3):
  print(sentences_en[i], "->", sentences_es[i])

He is a real fool. -> Él es un verdadero tonto.
It's very difficult to carry out that project. -> Es muy difícil realizar esa empresa.
We came back to camp before dark. -> Volvimos al campamento antes de que anocheciera.


In [9]:
vocab_size = 1000
max_length = 50
text_vec_layer_en = tf.keras.layers.TextVectorization(
    vocab_size, output_sequence_length=max_length)
text_vec_layer_es = tf.keras.layers.TextVectorization(
    vocab_size, output_sequence_length=max_length)
text_vec_layer_en.adapt(sentences_en)
text_vec_layer_es.adapt([f"startofseq {s} endofseq" for s in sentences_es])

In [10]:
X_train = tf.constant(sentences_en[:100_000])
X_valid = tf.constant(sentences_en[100_000:])
X_train_dec = tf.constant([f"startofseq {s}" for s in sentences_es[:100_000]])
X_valid_dec = tf.constant([f"startofseq {s}" for s in sentences_es[100_000:]])
Y_train = text_vec_layer_es([f"{s} endofseq" for s in sentences_es[:100_000]])
Y_valid = text_vec_layer_es([f"{s} endofseq" for s in sentences_es[100_000:]])

In [11]:
encoder_inputs = tf.keras.layers.Input(shape=[], dtype=tf.string)
decoder_inputs = tf.keras.layers.Input(shape=[], dtype=tf.string)

In [12]:
embed_size = 128
encoder_input_ids = text_vec_layer_en(encoder_inputs)
decoder_input_ids = text_vec_layer_es(decoder_inputs)
encoder_embedding_layer = tf.keras.layers.Embedding(vocab_size, embed_size, mask_zero=True)
decoder_embedding_layer = tf.keras.layers.Embedding(vocab_size, embed_size, mask_zero=True)
encoder_embeddings = encoder_embedding_layer(encoder_input_ids)
decoder_embeddings = decoder_embedding_layer(decoder_input_ids)

In [13]:
encoder = tf.keras.layers.LSTM(512, return_state=True)
encoder_outputs, *encoder_state = encoder(encoder_embeddings)
decoder = tf.keras.layers.LSTM(512, return_sequences=True)
decoder_outputs = decoder(decoder_embeddings, initial_state=encoder_state)

In [14]:
output_layer = tf.keras.layers.Dense(vocab_size, activation="softmax")
Y_proba = output_layer(decoder_outputs)

In [15]:
model = tf.keras.Model(inputs=[encoder_inputs, decoder_inputs], outputs=[Y_proba])
model.compile(optimizer="nadam", loss="sparse_categorical_crossentropy", metrics=["accuracy"])

In [16]:
model.fit((X_train, X_train_dec), Y_train, epochs=10, validation_data=((X_valid, X_valid_dec), Y_valid))

Epoch 1/10
3125/3125 [==============================] - 104s 29ms/step - loss: 2.9360 - accuracy: 0.4268 - val_loss: 2.1600 - val_accuracy: 0.5266
Epoch 2/10
3125/3125 [==============================] - 70s 22ms/step - loss: 1.8389 - accuracy: 0.5777 - val_loss: 1.6421 - val_accuracy: 0.6120
Epoch 3/10
3125/3125 [==============================] - 67s 21ms/step - loss: 1.4263 - accuracy: 0.6511 - val_loss: 1.4215 - val_accuracy: 0.6553
Epoch 4/10
3125/3125 [==============================] - 67s 22ms/step - loss: 1.1963 - accuracy: 0.6960 - val_loss: 1.3246 - val_accuracy: 0.6739
Epoch 5/10
3125/3125 [==============================] - 68s 22ms/step - loss: 1.0366 - accuracy: 0.7290 - val_loss: 1.2885 - val_accuracy: 0.6834
Epoch 6/10
3125/3125 [==============================] - 66s 21ms/step - loss: 0.9040 - accuracy: 0.7565 - val_loss: 1.2760 - val_accuracy: 0.6885
Epoch 7/10
3125/3125 [==============================] - 67s 22ms/step - loss: 0.7907 - accuracy: 0.7825 - val_loss: 1.2871 

In [17]:
def translate(sentence_en):
    translation = ""
    for word_idx in range(max_length):
        X = np.array([sentence_en]) # encoder input
        X_dec = np.array(["startofseq " + translation]) # decoder input
        y_proba = model.predict((X, X_dec))[0, word_idx] # last token's probas
        predicted_word_id = np.argmax(y_proba)
        predicted_word = text_vec_layer_es.get_vocabulary()[predicted_word_id]
        if predicted_word == "endofseq":
            break
        translation += " " + predicted_word
    return translation.strip()

In [21]:
translate("i like soccer")

1/1 [==============================] - 0s 21ms/step


'me gusta jugar'